In [ ]:
from __future__ import print_function, division
from keras.datasets import mnist
#from keras_contrib.layers.normalization.instancenormalization import InstanceNormalization
from keras.layers import Input,Dense,Reshape,Flatten,Dropout,Concatenate
from keras.layers import BatchNormalization,Activation,ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D,Conv2D
from keras.models import Sequential,Model
from keras.optimizers import Adam
from glob import glob 
import datetime
import matplotlib.pyplot as plt
import sys
import numpy as np 
import os 
import scipy
import scipy.misc
## condation is the second half of the image.
## we generate fake image on condation image
## img_B => condation 
## img_A => real image
## Discriminator(img_A,img_B) => Real
## Discriminator(fake_A,img_B) => Fake
## fake_A = Generator(img_B) generating fake images on condation images.
class DataLoader():
    def __init__(self,dataset_name,img_res=(128,128)):
        self.dataset_name = dataset_name
        self.img_res = img_res 
    def load_data(self,batch_size=1,is_testing=False):
        data_type = "train" if not is_testing else "test"
        path = glob('./datasets/%s/%s/*'%(self.dataset_name,data_type))
        batch_images = np.random.choice(path,size=batch_size)
        imgs_A = []
        imgs_B = []
        for img_path in batch_images:
            img = self.imread(img_path)
            h,w,_ = img.shape
            _w = int(w/2)
            img_A,img_B = img[:,:_w,:],img[:,_w:,:]
            img_A = scipy.misc.imresize(img_A,self.img_res)
            img_B = scipy.misc.imresize(img_B,self.img_res)
            # If training => do random flip
            if not is_testing and np.random.random() < 0.5:
                img_A = np.fliplr(img_A)
                img_B = np.fliplr(img_B)
            imgs_A.append(img_A)
            imgs_B.append(img_B)
        imgs_A = np.array(imgs_A)/127.5 - 1.
        imgs_B = np.array(imgs_B)/127.5 - 1.
        return imgs_A,imgs_B
    def load_batch(self,batch_size=1,is_testing=False):
        data_type = "train" if not is_testing else "val"
        path = glob('./datasets/%s/%s/*' % (self.dataset_name, data_type))
        self.n_batches = int(len(path)/batch_size)
        for i in range(self.n_batches-1):
            batch = path[i*batch_size:(i+1)*batch_size]
            imgs_A,imgs_B = [],[]
            for img in batch:
                img = self.imread(img)
                h,w,_ = img.shape
                half_w = int(w/2)
                img_A = img[:,:half_w,:]
                img_B = img[:,half_w:,:]
                img_A = scipy.misc.imresize(img_A,self.img_res)
                img_B = scipy.misc.imresize(img_B,self.img_res)
                if not is_testing and np.random.random() > 0.5:
                    img_A = np.fliplr(img_A)
                    img_B = np.fliplr(img_B)
                imgs_A.append(img_A)
                imgs_B.append(img_B)
            imgs_A = np.array(imgs_A)/127.5 - 1.
            imgs_B = np.array(imgs_B)/127.5 - 1.
            yield imgs_A,imgs_B 

    def imread(self,path):
        return scipy.misc.imread(path,mode='RGB').astype(np.float)


class Pix2Pix():
    def __init__(self):
        self.img_rows = 256
        self.img_cols = 256
        self.channels = 3
        self.img_shape = (self.img_rows,self.img_cols,self.channels)

        self.dataset_name = 'facades'
        self.data_loader = DataLoader(dataset_name=self.dataset_name,img_res=(self.img_rows,self.img_cols))
        # Calculate output shape of D (PatchGAN)
        patch = int(self.img_rows / 2**4)
        self.disc_patch = (patch,patch,1)
        # Number of filters in the first layer of G and D
        self.gf = 64
        self.df = 64
        
        optimizer = Adam(0.0002,0.5)

        # Build and compile the discriminator
        self.discriminator = self.build_discriminator()
        self.discriminator.compile(loss='mse',optimizer=optimizer,metrics=['accuracy'])
        #self.discriminator.summary()
        #------
        # Construct Computational
        # Graph of Generator
        #-------

        # Build the generator, generator don't have evaluating metrics.
        self.generator = self.build_generator()
        
        #self.generator.summary()
        # Input images and their conditioning images

        img_A = Input(shape=self.img_shape)
        img_B = Input(shape=self.img_shape)

        # By conditioning on B generate a fake version of A 
        fake_A = self.generator(img_B)

        # For the combined model we will only train the generator
        self.discriminator.trainable = False

        # Discriminators determines validity of translated images / condition pairs
        valid = self.discriminator([fake_A,img_B])

        self.combined = Model(inputs=[img_A,img_B],outputs=[valid,fake_A])
        # 'mse'== 'mean squared error' 'mae' == 'mean absolute error'
        self.combined.compile(loss=['mse','mae'],loss_weights=[1,100],optimizer=optimizer)
        self.combined.summary()
    def build_generator(self):
        """U-Net Generator"""

        def conv2d(layer_input,filters,f_size=4,bn=True):
            """Layers used during downsampling"""
            d = Conv2D(filters,kernel_size=f_size,strides=2,padding='same')(layer_input)
            d = LeakyReLU(alpha=0.2)(d)
            if bn:
                d = BatchNormalization(momentum=0.8)(d)
            return d 
        def deconv2d(layer_input,skip_input,filters,f_size=4,dropout_rate=0):
            """Layers used during upsampling"""
            u = UpSampling2D(size=2)(layer_input)
            u = Conv2D(filters,kernel_size=f_size,strides=1,padding='same',activation='relu')(u)
            if dropout_rate:
                u = DropOut(dropout_rate)(u)
            u = BatchNormalization(momentum=0.8)(u)
            u = Concatenate()([u,skip_input])
            return u
        # Image input
        d0 = Input(shape=self.img_shape)
        # Downsampling
        d1 = conv2d(d0,self.gf,bn=False)
        d2 = conv2d(d1,self.gf*2)
        d3 = conv2d(d2,self.gf*4)
        d4 = conv2d(d3,self.gf*8)
        d5 = conv2d(d4,self.gf*8)
        d6 = conv2d(d5,self.gf*8)
        d7 = conv2d(d6,self.gf*8)

        # Upsampling

        u1 = deconv2d(d7,d6,self.gf*8)
        u2 = deconv2d(u1,d5,self.gf*8)
        u3 = deconv2d(u2,d4,self.gf*8)
        u4 = deconv2d(u3,d3,self.gf*4)
        u5 = deconv2d(u4,d2,self.gf*2)
        u6 = deconv2d(u5,d1,self.df)

        u7 = UpSampling2D(size=2)(u6)
        output_img = Conv2D(self.channels,kernel_size=4,strides=1,padding='same',activation='tanh')(u7)
        return Model(d0,output_img)
    def build_discriminator(self):
        def d_layer(layer_input,filters,f_size=4,bn=True):
            """Discriminator layer"""
            d = Conv2D(filters,kernel_size=f_size,strides=2,padding='same')(layer_input)
            d = LeakyReLU(alpha=0.2)(d)
            if bn:
                d = BatchNormalization(momentum=0.8)(d)
            return d 

        img_A = Input(shape=self.img_shape)
        img_B = Input(shape=self.img_shape)
        # Concatenate image and conditioning image by channels to produce input
        combined_imgs = Concatenate(axis=-1)([img_A,img_B])

        d1 = d_layer(combined_imgs,self.df,bn=False)
        d2 = d_layer(d1,self.df*2)
        d3 = d_layer(d2,self.df*4)
        d4 = d_layer(d3,self.df*8)

        validity = Conv2D(1,kernel_size=4,strides=1,padding='same')(d4)
        return Model([img_A,img_B],validity)

    def train(self,epochs,batch_size=1,sample_interval=50):
        start_time = datetime.datetime.now()

        # Adversarial loss ground truths
        valid = np.ones((batch_size,)+self.disc_patch)
        fake = np.zeros((batch_size,)+self.disc_patch)

        for epoch in range(epochs):
            for batch_i,(imgs_A,imgs_B) in enumerate(self.data_loader.load_batch(batch_size)):
                # _-----
                # Train Discriminator
                # ----
                # Condition on B and generate a translated version

                fake_A = self.generator.predict(imgs_B)

                # Train the discriminators (original images = real / generated = Fake)
                d_loss_real = self.discriminator.train_on_batch([imgs_A,imgs_B],valid)
                d_loss_fake = self.discriminator.train_on_batch([fake_A,imgs_B],fake)
                d_loss = 0.5 * np.add(d_loss_real,d_loss_fake)

                # --------
                # Train Generator
                # --------

                # Train the generators 

                g_loss = self.combined.train_on_batch([imgs_A,imgs_B],[valid,imgs_A])
                elapsed_time = datetime.datetime.now() - start_time

                # Plot the progress

                print("[Epoch %d/%d] [Batch %d/%d] [D loss: %f, acc: %3d%%] [G loss: %f] time: %s" % (epoch,epochs,batch_i,self.data_loader.n_batches,d_loss[0],100*d_loss[1],g_loss[0],elapsed_time))

                # If at save interval => save generated image samples 
                """
                if batch_i % sample_interval == 0:
                    self.generator.save('generator.h5')
                    self.sample_images(epoch,batch_i)
                """
            if epoch % 20 == 0:
                self.generator.save(f'generator{epoch}.h5')
                self.sample_images(epoch,batch_i)
            
    def sample_images(self,epoch,batch_i):
        os.makedirs('images/%s' % self.dataset_name,exist_ok=True)
        r,c = 3,3
        imgs_A,imgs_B = self.data_loader.load_data(batch_size=3,is_testing=True)
        fake_A = self.generator.predict(imgs_B)

        gen_imgs = np.concatenate([imgs_B,fake_A,imgs_A])

        # Rescale images 0-1
        gen_imgs = 0.5 * gen_imgs + 0.5
        titles = ['Condition','Generated','Original']
        fig,axs = plt.subplots(r,c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt])
                axs[i,j].set_title(titles[i])
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("images/%s/%d_%d.png" % (self.dataset_name, epoch, batch_i))
        plt.close()

if __name__ == '__main__':
    gan = Pix2Pix()
    gan.train(epochs=200,batch_size=1,sample_interval=200)
    #gan.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_53 (InputLayer)           (None, 256, 256, 3)  0                                            
__________________________________________________________________________________________________
model_30 (Model)                (None, 256, 256, 3)  41843331    input_53[0][0]                   
__________________________________________________________________________________________________
model_29 (Model)                (None, 16, 16, 1)    2771393     model_30[1][0]                   
                                                                 input_53[0][0]                   
Total params: 44,614,724
Trainable params: 41,834,499
Non-trainable params: 2,780,225
__________________________________________________________________________________________________


/home/zsh/anaconda3/envs/zshocr/lib/python3.6/site-packages/ipykernel_launcher.py:76: DeprecationWarning: `imread` is deprecated!
`imread` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imread`` instead.
/home/zsh/anaconda3/envs/zshocr/lib/python3.6/site-packages/ipykernel_launcher.py:64: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.
/home/zsh/anaconda3/envs/zshocr/lib/python3.6/site-packages/ipykernel_launcher.py:65: DeprecationWarning: `imresize` is deprecated!
`imresize` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``skimage.transform.resize`` instead.


[Epoch 0/200] [Batch 0/400] [D loss: 14.537269, acc:  15%] [G loss: 67.874069] time: 0:00:15.782408
[Epoch 0/200] [Batch 1/400] [D loss: 3.948571, acc:  18%] [G loss: 80.965721] time: 0:00:15.913089
[Epoch 0/200] [Batch 2/400] [D loss: 3.851418, acc:  19%] [G loss: 68.389252] time: 0:00:16.043131
[Epoch 0/200] [Batch 3/400] [D loss: 5.487986, acc:  18%] [G loss: 76.892563] time: 0:00:16.167440
[Epoch 0/200] [Batch 4/400] [D loss: 3.089843, acc:  20%] [G loss: 71.162804] time: 0:00:16.291633
[Epoch 0/200] [Batch 5/400] [D loss: 2.534793, acc:  22%] [G loss: 60.744423] time: 0:00:16.416832
[Epoch 0/200] [Batch 6/400] [D loss: 3.079797, acc:  23%] [G loss: 63.822277] time: 0:00:16.539373
[Epoch 0/200] [Batch 7/400] [D loss: 2.458789, acc:  27%] [G loss: 53.764080] time: 0:00:16.659585
[Epoch 0/200] [Batch 8/400] [D loss: 3.618608, acc:  28%] [G loss: 59.972336] time: 0:00:16.783073
[Epoch 0/200] [Batch 9/400] [D loss: 3.349241, acc:  24%] [G loss: 62.365589] time: 0:00:16.903195
[Epoch 0/

[Epoch 0/200] [Batch 84/400] [D loss: 0.520881, acc:  46%] [G loss: 35.842739] time: 0:00:26.196629
[Epoch 0/200] [Batch 85/400] [D loss: 0.445041, acc:  53%] [G loss: 43.536739] time: 0:00:26.318298
[Epoch 0/200] [Batch 86/400] [D loss: 0.337945, acc:  53%] [G loss: 32.640347] time: 0:00:26.442270
[Epoch 0/200] [Batch 87/400] [D loss: 0.381355, acc:  55%] [G loss: 40.580002] time: 0:00:26.563044
[Epoch 0/200] [Batch 88/400] [D loss: 0.409073, acc:  47%] [G loss: 38.947731] time: 0:00:26.685134
[Epoch 0/200] [Batch 89/400] [D loss: 0.497674, acc:  36%] [G loss: 40.886223] time: 0:00:26.807180
[Epoch 0/200] [Batch 90/400] [D loss: 0.369834, acc:  53%] [G loss: 41.065659] time: 0:00:26.928702
[Epoch 0/200] [Batch 91/400] [D loss: 0.415712, acc:  48%] [G loss: 36.450802] time: 0:00:27.047758
[Epoch 0/200] [Batch 92/400] [D loss: 0.414184, acc:  53%] [G loss: 23.422880] time: 0:00:27.167486
[Epoch 0/200] [Batch 93/400] [D loss: 0.541669, acc:  32%] [G loss: 40.242516] time: 0:00:27.295694


[Epoch 0/200] [Batch 166/400] [D loss: 0.373437, acc:  43%] [G loss: 42.244888] time: 0:00:36.455960
[Epoch 0/200] [Batch 167/400] [D loss: 0.357297, acc:  51%] [G loss: 43.316811] time: 0:00:36.582334
[Epoch 0/200] [Batch 168/400] [D loss: 0.315585, acc:  58%] [G loss: 37.656559] time: 0:00:36.703923
[Epoch 0/200] [Batch 169/400] [D loss: 0.360774, acc:  43%] [G loss: 31.571474] time: 0:00:36.825567
[Epoch 0/200] [Batch 170/400] [D loss: 0.464291, acc:  46%] [G loss: 23.818571] time: 0:00:36.947198
[Epoch 0/200] [Batch 171/400] [D loss: 0.343787, acc:  50%] [G loss: 36.551476] time: 0:00:37.068375
[Epoch 0/200] [Batch 172/400] [D loss: 0.287362, acc:  55%] [G loss: 33.990742] time: 0:00:37.190581
[Epoch 0/200] [Batch 173/400] [D loss: 0.278600, acc:  60%] [G loss: 37.725056] time: 0:00:37.311616
[Epoch 0/200] [Batch 174/400] [D loss: 0.310393, acc:  50%] [G loss: 31.442907] time: 0:00:37.435877
[Epoch 0/200] [Batch 175/400] [D loss: 0.481895, acc:  46%] [G loss: 45.285084] time: 0:00:

...

[Epoch 114/200] [Batch 237/400] [D loss: 0.000619, acc: 100%] [G loss: 13.811118] time: 1:34:14.560653
[Epoch 114/200] [Batch 238/400] [D loss: 0.000311, acc: 100%] [G loss: 14.513406] time: 1:34:14.680651
[Epoch 114/200] [Batch 239/400] [D loss: 0.000364, acc: 100%] [G loss: 14.263421] time: 1:34:14.801521
[Epoch 114/200] [Batch 240/400] [D loss: 0.000163, acc: 100%] [G loss: 11.632077] time: 1:34:14.925036
[Epoch 114/200] [Batch 241/400] [D loss: 0.013197, acc: 100%] [G loss: 10.828560] time: 1:34:15.048310
[Epoch 114/200] [Batch 242/400] [D loss: 0.001948, acc: 100%] [G loss: 15.387488] time: 1:34:15.168571
[Epoch 114/200] [Batch 243/400] [D loss: 0.000765, acc: 100%] [G loss: 16.460947] time: 1:34:15.290831
[Epoch 114/200] [Batch 244/400] [D loss: 0.000510, acc: 100%] [G loss: 16.328968] time: 1:34:15.410919
[Epoch 114/200] [Batch 245/400] [D loss: 0.000297, acc: 100%] [G loss: 14.176873] time: 1:34:15.532277
[Epoch 114/200] [Batch 246/400] [D loss: 0.000696, acc: 100%] [G loss: 12

[Epoch 114/200] [Batch 317/400] [D loss: 0.000185, acc: 100%] [G loss: 14.041551] time: 1:34:24.366582
[Epoch 114/200] [Batch 318/400] [D loss: 0.000248, acc: 100%] [G loss: 9.877788] time: 1:34:24.488039
[Epoch 114/200] [Batch 319/400] [D loss: 0.000147, acc: 100%] [G loss: 13.689134] time: 1:34:24.609023
[Epoch 114/200] [Batch 320/400] [D loss: 0.000347, acc: 100%] [G loss: 11.006650] time: 1:34:24.730994
[Epoch 114/200] [Batch 321/400] [D loss: 0.000390, acc: 100%] [G loss: 9.391830] time: 1:34:24.852258
[Epoch 114/200] [Batch 322/400] [D loss: 0.000146, acc: 100%] [G loss: 15.363999] time: 1:34:24.977266
[Epoch 114/200] [Batch 323/400] [D loss: 0.000105, acc: 100%] [G loss: 15.477475] time: 1:34:25.101278
[Epoch 114/200] [Batch 324/400] [D loss: 0.000210, acc: 100%] [G loss: 12.520565] time: 1:34:25.229466
[Epoch 114/200] [Batch 325/400] [D loss: 0.000121, acc: 100%] [G loss: 11.518572] time: 1:34:25.351542
[Epoch 114/200] [Batch 326/400] [D loss: 0.000092, acc: 100%] [G loss: 9.52

[Epoch 114/200] [Batch 397/400] [D loss: 0.000158, acc: 100%] [G loss: 12.996448] time: 1:34:34.261338
[Epoch 114/200] [Batch 398/400] [D loss: 0.000264, acc: 100%] [G loss: 12.797900] time: 1:34:34.387156
[Epoch 115/200] [Batch 0/400] [D loss: 0.000129, acc: 100%] [G loss: 12.724524] time: 1:34:34.508665
[Epoch 115/200] [Batch 1/400] [D loss: 0.000130, acc: 100%] [G loss: 15.961342] time: 1:34:34.629371
[Epoch 115/200] [Batch 2/400] [D loss: 0.000308, acc: 100%] [G loss: 12.029917] time: 1:34:34.751906
[Epoch 115/200] [Batch 3/400] [D loss: 0.000389, acc: 100%] [G loss: 13.953253] time: 1:34:34.874910
[Epoch 115/200] [Batch 4/400] [D loss: 0.000110, acc: 100%] [G loss: 12.820270] time: 1:34:34.998621
[Epoch 115/200] [Batch 5/400] [D loss: 0.000252, acc: 100%] [G loss: 11.220544] time: 1:34:35.119478
[Epoch 115/200] [Batch 6/400] [D loss: 0.000344, acc: 100%] [G loss: 10.391784] time: 1:34:35.242189
[Epoch 115/200] [Batch 7/400] [D loss: 0.000355, acc: 100%] [G loss: 8.136729] time: 1:

[Epoch 115/200] [Batch 80/400] [D loss: 0.000201, acc: 100%] [G loss: 14.074525] time: 1:34:44.360108
[Epoch 115/200] [Batch 81/400] [D loss: 0.000155, acc: 100%] [G loss: 13.376328] time: 1:34:44.480675
[Epoch 115/200] [Batch 82/400] [D loss: 0.000257, acc: 100%] [G loss: 10.691879] time: 1:34:44.602480
[Epoch 115/200] [Batch 83/400] [D loss: 0.000099, acc: 100%] [G loss: 10.816204] time: 1:34:44.723778
[Epoch 115/200] [Batch 84/400] [D loss: 0.000178, acc: 100%] [G loss: 10.544068] time: 1:34:44.846508
[Epoch 115/200] [Batch 85/400] [D loss: 0.000133, acc: 100%] [G loss: 14.853944] time: 1:34:44.967927
[Epoch 115/200] [Batch 86/400] [D loss: 0.000628, acc: 100%] [G loss: 9.944908] time: 1:34:45.090412
[Epoch 115/200] [Batch 87/400] [D loss: 0.000749, acc: 100%] [G loss: 10.284503] time: 1:34:45.212515
[Epoch 115/200] [Batch 88/400] [D loss: 0.000561, acc: 100%] [G loss: 17.887543] time: 1:34:45.335299
[Epoch 115/200] [Batch 89/400] [D loss: 0.000279, acc: 100%] [G loss: 12.291415] ti

[Epoch 115/200] [Batch 160/400] [D loss: 0.000231, acc: 100%] [G loss: 14.097693] time: 1:34:54.204430
[Epoch 115/200] [Batch 161/400] [D loss: 0.000111, acc: 100%] [G loss: 15.617157] time: 1:34:54.331764
[Epoch 115/200] [Batch 162/400] [D loss: 0.000106, acc: 100%] [G loss: 15.193768] time: 1:34:54.453964
[Epoch 115/200] [Batch 163/400] [D loss: 0.000091, acc: 100%] [G loss: 11.455553] time: 1:34:54.573494
[Epoch 115/200] [Batch 164/400] [D loss: 0.000080, acc: 100%] [G loss: 13.136267] time: 1:34:54.694919
[Epoch 115/200] [Batch 165/400] [D loss: 0.000128, acc: 100%] [G loss: 14.625714] time: 1:34:54.816955
[Epoch 115/200] [Batch 166/400] [D loss: 0.000169, acc: 100%] [G loss: 17.499821] time: 1:34:54.964705
[Epoch 115/200] [Batch 167/400] [D loss: 0.000194, acc: 100%] [G loss: 15.210663] time: 1:34:55.084930
[Epoch 115/200] [Batch 168/400] [D loss: 0.000145, acc: 100%] [G loss: 13.669834] time: 1:34:55.211126
[Epoch 115/200] [Batch 169/400] [D loss: 0.000295, acc: 100%] [G loss: 12

In [1]:
import numpy as np 

disc_patch = (16,16,1)
valid = np.ones((1,)+disc_patch)
print(f'valid shape {valid.shape}')

valid shape (1, 16, 16, 1)


In [1]:
!nvidia-smi

Fri Feb 14 21:11:05 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.33.01    Driver Version: 440.33.01    CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  GeForce GTX 108...  Off  | 00000000:01:00.0  On |                  N/A |
| 21%   35C    P8    11W / 250W |    325MiB / 11175MiB |      2%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [1]:
import keras
from keras.models import load_model

Using TensorFlow backend.
/home/zsh/anaconda3/envs/zshocr/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/zsh/anaconda3/envs/zshocr/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/zsh/anaconda3/envs/zshocr/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/zsh/anaconda3/envs/zsho